In [1]:
import os
os.getcwd()


'/projects/alar6830/SwiFT'

In [2]:
import math
## if onset time is between frames, use the next available frame

def frame_to_seconds(frame):
    return math.ceil * 0.72

def seconds_to_frame(sec):
    return math.ceil(sec/.72)

In [3]:
path = "/scratch/alpine/alar6830"
print(os.path.exists(path))

True


In [3]:
import pandas as pd

# get the list of downloaded file name


#get data for downstream tasks
behavior_data = pd.read_csv("unrestricted_hcp_freesurfer.csv")
behavior_data.head(5)
subject_values = behavior_data['Subject'].values

def check_file_name(file_name, downloaded_files):
  for file_name_path in downloaded_files:
    if file_name in file_name_path:
      return True
  return False
print(len(subject_values))

1113


In [4]:
import subprocess

def check_s3_path_exists(bucket_name, path):
    aws_command = f"aws s3 ls s3://{bucket_name}/{path}"
    try:
        # Run the command and capture output
        result = subprocess.run(aws_command, shell=True, capture_output=True, text=True)
        
        # If the command returns 0, the path exists; otherwise, it doesn't
        if result.returncode == 0 and result.stdout.strip():
            return True
        else:
            return False
    except Exception as e:
        print(f"Error checking path {path}: {e}")
        return False


In [ ]:
# Loop over subject values
bucket_name = 'hcp-openaccess'

count = 0
for subject in subject_values:
    s3_path = f"HCP_1200/{subject}/MNINonLinear/Results/tfMRI_WM_LR/"
    if check_s3_path_exists(bucket_name, s3_path):
        print(f"Path exists: {s3_path}")
        count+=1
    else:
        print(f"Path NOT found: {s3_path}")

In [ ]:
print(count)

aws_command = f"aws s3 cp s3://hcp-openaccess/HCP_1200/{subject}/MNINonLinear/Results/tfMRI_WM_LR/WM_run2_TAB.txt ./projects/alar6830/WM_run.txt"
!{aws_command}
aws_command = f"aws s3 cp  s3://hcp-openaccess/HCP_1200/{subject}/MNINonLinear/Results/tfMRI_WM_LR/EVs/ ./projects/alar6830/ --recursive"
!{aws_command}


import numpy as np
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
wm = pd.read_csv("./projects/alar6830/WM_run.txt", sep = "\t")
wm


procedures = wm["Procedure[Block]"]
trialTypes = wm["TargetType"]
trialOnsetTimes = wm["ExperimenterWindow.OnsetTime"]
initialOnsets = wm["SyncSlide.OnsetTime"]
initialFinishes = wm["SyncSlide.FinishTime"]
# things to dump
durations = []
procedureNames = []
trialNames = []

restOffset = 4
cueDuration = 2500
fixRestDuration = 15000

# durations
# initial rest
durations.append(initialFinishes[restOffset-1] - initialOnsets[0])
procedureNames.append("REST")
trialNames.append("REST")

restDuration = 0

for i, trialOnset in enumerate(trialOnsetTimes[restOffset:]):

	
	procedure = procedures[i+restOffset]
	trialName = trialTypes[i+restOffset]

	if(np.isnan(trialOnset)):

		if("Cue" in procedure):
			restDuration = cueDuration
		else:
			restDuration = fixRestDuration

		durations.append(restDuration)
		procedureNames.append("REST")
		trialNames.append("REST")
			
	else:
		if(i+restOffset+1 < len(trialOnsetTimes) and not np.isnan(trialOnsetTimes[restOffset+i+1])):
			trialDuration = trialOnsetTimes[i+restOffset+1] - trialOnset

		durations.append(trialDuration)
		procedureNames.append(procedure)
		trialNames.append(trialName)

data = pd.DataFrame({"durations":durations , "procedure": procedureNames, " trial":trialNames})
data

data['durations'][:24].sum()/1000

import nibabel as nib
image_path = f"/scratch/alpine/alar6830/WM_LR/{subject}/{subject}_WM_LR.nii.gz"
nib.load(image_path).get_fdata().shape[3] *.72



In [12]:
import os
subject_values = behavior_data['Subject'].values


bucket_name = 'hcp-openaccess'

count = 0
for subject in subject_values:
    root = f"/scratch/alpine/alar6830/WM_All/{subject}/"
    RL_root = os.path.join(root, "RL")
    LR_root = os.path.join(root, "LR")
    
    
    if not os.path.exists(root):
        os.mkdir(root)
        os.mkdir(RL_root)
        os.mkdir(LR_root)
    if os.path.exists(f"/scratch/alpine/alar6830/WM_All/{subject}/RL/tfMRI_WM_RL.nii.gz"):
        
        print("already did "+str(subject))
        continue
    s3_path = f"HCP_1200/{subject}/MNINonLinear/Results/tfMRI_WM_LR/tfMRI_WM_LR.nii.gz"
    if check_s3_path_exists(bucket_name, s3_path):
        
        path = f"s3://{bucket_name}/{s3_path}"
        file ="tfMRI_WM_LR.nii.gz"
        aws_command = f"aws s3 cp {path} {os.path.join(LR_root, file )}"
        !{aws_command}
        count+=1
    else:
        print(f"Path NOT found: {s3_path}")
    s3_path = f"HCP_1200/{subject}/MNINonLinear/Results/tfMRI_WM_RL/tfMRI_WM_RL.nii.gz"
    if check_s3_path_exists(bucket_name, s3_path):
        file  = "tfMRI_WM_RL.nii.gz"
        path = f"s3://{bucket_name}/{s3_path}"
        aws_command = f"aws s3 cp {path} {os.path.join(RL_root, file )}"
        !{aws_command}
        count+=1
    else:
        print(f"Path NOT found: {s3_path}")
    
    if(count %20 == 0):
        print()
        print(count)
        print()

print(count)
  # subject_name = subject_name.rstrip()

#   file_name = "tfMRI_WM_LR.nii.gz"

#   download_path = f"/scratch/alpine/alar6830/WM_LR/{subject_name}/"
#   if not os.path.exists(download_path):
#     os.makedirs(download_path)
#   full_download_path = download_path + f"{subject_name}_WM_LR.nii.gz"
# aws_command = f"aws s3 cp s3://hcp-openaccess/HCP_1200/{subject_name}/MNINonLinear/Results/tfMRI_WM_LR/{file_name} {full_download_path}"
#   !{aws_command}
  
#   aws_command = f"aws s3 cp  s3://hcp-openaccess/HCP_1200/{subject_name}/MNINonLinear/Results/tfMRI_WM_LR/EVs/ {download_path} --recursive"
#   !{aws_command}
#   if(count ==100):
#     break


already did 100206
already did 100307
already did 100408
already did 100610
already did 101006
already did 101107
already did 101309
already did 101410
already did 101915
already did 102008
already did 102109
already did 102311
already did 102513
already did 102614
already did 102715
already did 102816
already did 103010
already did 103111
already did 103212
already did 103414
already did 103515
already did 103818
already did 104012
already did 104416
already did 104820
already did 105014
already did 105115
already did 105216
already did 105620
already did 105923
already did 106016
already did 106319
already did 106521
already did 106824
already did 107018
already did 107220
already did 107321
already did 107422
already did 107725
already did 108020
already did 108121
already did 108222
already did 108323
already did 108525
already did 108828
already did 109123
already did 109325
already did 109830
already did 110007
already did 110411
already did 110613
already did 111009
already did 

download: s3://hcp-openaccess/HCP_1200/185846/MNINonLinear/Results/tfMRI_WM_LR/tfMRI_WM_LR.nii.gz to ../../../scratch/alpine/alar6830/WM_All/185846/LR/tfMRI_WM_LR.nii.gz
Path NOT found: HCP_1200/185846/MNINonLinear/Results/tfMRI_WM_RL/tfMRI_WM_RL.nii.gz
already did 185947
already did 186040
already did 186141
already did 186444
already did 186545
already did 186848
already did 186949
already did 187143
already did 187345
already did 187547
already did 187850
already did 188145
already did 188347
already did 188448
already did 188549
already did 188751
already did 189349
already did 189450
already did 189652
already did 190031
Path NOT found: HCP_1200/190132/MNINonLinear/Results/tfMRI_WM_LR/tfMRI_WM_LR.nii.gz
Path NOT found: HCP_1200/190132/MNINonLinear/Results/tfMRI_WM_RL/tfMRI_WM_RL.nii.gz
already did 191033
already did 191235
already did 191336
already did 191437
already did 191841
already did 191942
already did 192035
already did 192136
already did 192237
already did 192439
already 

already did 566454
already did 567052
already did 567759
already did 567961
already did 568963
already did 569965
already did 570243
already did 571144
Path NOT found: HCP_1200/571548/MNINonLinear/Results/tfMRI_WM_LR/tfMRI_WM_LR.nii.gz
Path NOT found: HCP_1200/571548/MNINonLinear/Results/tfMRI_WM_RL/tfMRI_WM_RL.nii.gz
already did 572045
already did 573249
already did 573451
already did 576255
already did 578057
already did 578158
already did 579665
already did 579867
already did 580044
already did 580347
already did 580650
already did 580751
already did 581349
already did 581450
already did 583858
Path NOT found: HCP_1200/584355/MNINonLinear/Results/tfMRI_WM_LR/tfMRI_WM_LR.nii.gz
Path NOT found: HCP_1200/584355/MNINonLinear/Results/tfMRI_WM_RL/tfMRI_WM_RL.nii.gz
already did 585256
already did 585862
already did 586460
already did 587664
already did 588565
already did 589567
already did 590047
already did 592455
already did 594156
already did 597869
already did 598568
already did 599065

In [8]:
for subject in subject_values:
    if not os.path.exists(f"/scratch/alpine/alar6830/WM_All/{subject}/RL/tfMRI_WM_RL.nii.gz"):
        print()
        print("no file for "+str(subject))
        print()
        continue
    
    print(subject)
    LR_path = f"/scratch/alpine/alar6830/WM_All/{subject}/LR/metadata"
    if not os.path.exists(LR_path):
        os.mkdir(LR_path)
    aws_command = f"aws s3 cp  s3://hcp-openaccess/HCP_1200/{subject}/MNINonLinear/Results/tfMRI_WM_LR/EVs/ {LR_path} --recursive"
    !{aws_command}
    
    RL_path = f"/scratch/alpine/alar6830/WM_All/{subject}/RL/metadata"
    if not os.path.exists(RL_path):
        os.mkdir(RL_path)
    aws_command = f"aws s3 cp  s3://hcp-openaccess/HCP_1200/{subject}/MNINonLinear/Results/tfMRI_WM_RL/EVs/ {RL_path} --recursive"
    !{aws_command}
    

100206
download: s3://hcp-openaccess/HCP_1200/100206/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_tools.txt to ../../../scratch/alpine/alar6830/WM_All/100206/LR/metadata/0bk_tools.txt
download: s3://hcp-openaccess/HCP_1200/100206/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_body.txt to ../../../scratch/alpine/alar6830/WM_All/100206/LR/metadata/0bk_body.txt
download: s3://hcp-openaccess/HCP_1200/100206/MNINonLinear/Results/tfMRI_WM_LR/EVs/2bk_faces.txt to ../../../scratch/alpine/alar6830/WM_All/100206/LR/metadata/2bk_faces.txt
download: s3://hcp-openaccess/HCP_1200/100206/MNINonLinear/Results/tfMRI_WM_LR/EVs/2bk_nlr.txt to ../../../scratch/alpine/alar6830/WM_All/100206/LR/metadata/2bk_nlr.txt
download: s3://hcp-openaccess/HCP_1200/100206/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_places.txt to ../../../scratch/alpine/alar6830/WM_All/100206/LR/metadata/0bk_places.txt
download: s3://hcp-openaccess/HCP_1200/100206/MNINonLinear/Results/tfMRI_WM_LR/EVs/2bk_err.txt to ../../../scratch/alpine/alar6830/W

download: s3://hcp-openaccess/HCP_1200/100307/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_cor.txt to ../../../scratch/alpine/alar6830/WM_All/100307/LR/metadata/0bk_cor.txt
download: s3://hcp-openaccess/HCP_1200/100307/MNINonLinear/Results/tfMRI_WM_LR/EVs/all_bk_cor.txt to ../../../scratch/alpine/alar6830/WM_All/100307/LR/metadata/all_bk_cor.txt
download: s3://hcp-openaccess/HCP_1200/100307/MNINonLinear/Results/tfMRI_WM_RL/EVs/0bk_body.txt to ../../../scratch/alpine/alar6830/WM_All/100307/RL/metadata/0bk_body.txt
download: s3://hcp-openaccess/HCP_1200/100307/MNINonLinear/Results/tfMRI_WM_RL/EVs/2bk_faces.txt to ../../../scratch/alpine/alar6830/WM_All/100307/RL/metadata/2bk_faces.txt
download: s3://hcp-openaccess/HCP_1200/100307/MNINonLinear/Results/tfMRI_WM_RL/EVs/0bk_places.txt to ../../../scratch/alpine/alar6830/WM_All/100307/RL/metadata/0bk_places.txt
download: s3://hcp-openaccess/HCP_1200/100307/MNINonLinear/Results/tfMRI_WM_RL/EVs/2bk_body.txt to ../../../scratch/alpine/alar6830/WM_Al

download: s3://hcp-openaccess/HCP_1200/100408/MNINonLinear/Results/tfMRI_WM_RL/EVs/Sync.txt to ../../../scratch/alpine/alar6830/WM_All/100408/RL/metadata/Sync.txt
100610
download: s3://hcp-openaccess/HCP_1200/100610/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_places.txt to ../../../scratch/alpine/alar6830/WM_All/100610/LR/metadata/0bk_places.txt
download: s3://hcp-openaccess/HCP_1200/100610/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_body.txt to ../../../scratch/alpine/alar6830/WM_All/100610/LR/metadata/0bk_body.txt
download: s3://hcp-openaccess/HCP_1200/100610/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_tools.txt to ../../../scratch/alpine/alar6830/WM_All/100610/LR/metadata/0bk_tools.txt
download: s3://hcp-openaccess/HCP_1200/100610/MNINonLinear/Results/tfMRI_WM_LR/EVs/2bk_nlr.txt to ../../../scratch/alpine/alar6830/WM_All/100610/LR/metadata/2bk_nlr.txt
download: s3://hcp-openaccess/HCP_1200/100610/MNINonLinear/Results/tfMRI_WM_LR/EVs/2bk_places.txt to ../../../scratch/alpine/alar6830/WM_All/1

download: s3://hcp-openaccess/HCP_1200/101006/MNINonLinear/Results/tfMRI_WM_LR/EVs/Sync.txt to ../../../scratch/alpine/alar6830/WM_All/101006/LR/metadata/Sync.txt
download: s3://hcp-openaccess/HCP_1200/101006/MNINonLinear/Results/tfMRI_WM_LR/EVs/all_bk_err.txt to ../../../scratch/alpine/alar6830/WM_All/101006/LR/metadata/all_bk_err.txt
download: s3://hcp-openaccess/HCP_1200/101006/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_faces.txt to ../../../scratch/alpine/alar6830/WM_All/101006/LR/metadata/0bk_faces.txt
download: s3://hcp-openaccess/HCP_1200/101006/MNINonLinear/Results/tfMRI_WM_LR/EVs/WM_Stats.csv to ../../../scratch/alpine/alar6830/WM_All/101006/LR/metadata/WM_Stats.csv
download: s3://hcp-openaccess/HCP_1200/101006/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_cor.txt to ../../../scratch/alpine/alar6830/WM_All/101006/LR/metadata/0bk_cor.txt
download: s3://hcp-openaccess/HCP_1200/101006/MNINonLinear/Results/tfMRI_WM_LR/EVs/all_bk_cor.txt to ../../../scratch/alpine/alar6830/WM_All/101006/L

download: s3://hcp-openaccess/HCP_1200/101107/MNINonLinear/Results/tfMRI_WM_RL/EVs/0bk_err.txt to ../../../scratch/alpine/alar6830/WM_All/101107/RL/metadata/0bk_err.txt
download: s3://hcp-openaccess/HCP_1200/101107/MNINonLinear/Results/tfMRI_WM_RL/EVs/0bk_nlr.txt to ../../../scratch/alpine/alar6830/WM_All/101107/RL/metadata/0bk_nlr.txt
download: s3://hcp-openaccess/HCP_1200/101107/MNINonLinear/Results/tfMRI_WM_RL/EVs/0bk_faces.txt to ../../../scratch/alpine/alar6830/WM_All/101107/RL/metadata/0bk_faces.txt
download: s3://hcp-openaccess/HCP_1200/101107/MNINonLinear/Results/tfMRI_WM_RL/EVs/Sync.txt to ../../../scratch/alpine/alar6830/WM_All/101107/RL/metadata/Sync.txt
download: s3://hcp-openaccess/HCP_1200/101107/MNINonLinear/Results/tfMRI_WM_RL/EVs/WM_Stats.csv to ../../../scratch/alpine/alar6830/WM_All/101107/RL/metadata/WM_Stats.csv
download: s3://hcp-openaccess/HCP_1200/101107/MNINonLinear/Results/tfMRI_WM_RL/EVs/0bk_cor.txt to ../../../scratch/alpine/alar6830/WM_All/101107/RL/metadat

...

download: s3://hcp-openaccess/HCP_1200/991267/MNINonLinear/Results/tfMRI_WM_RL/EVs/0bk_body.txt to ../../../scratch/alpine/alar6830/WM_All/991267/RL/metadata/0bk_body.txt
download: s3://hcp-openaccess/HCP_1200/991267/MNINonLinear/Results/tfMRI_WM_RL/EVs/0bk_places.txt to ../../../scratch/alpine/alar6830/WM_All/991267/RL/metadata/0bk_places.txt
download: s3://hcp-openaccess/HCP_1200/991267/MNINonLinear/Results/tfMRI_WM_RL/EVs/2bk_cor.txt to ../../../scratch/alpine/alar6830/WM_All/991267/RL/metadata/2bk_cor.txt
download: s3://hcp-openaccess/HCP_1200/991267/MNINonLinear/Results/tfMRI_WM_RL/EVs/2bk_body.txt to ../../../scratch/alpine/alar6830/WM_All/991267/RL/metadata/2bk_body.txt
download: s3://hcp-openaccess/HCP_1200/991267/MNINonLinear/Results/tfMRI_WM_RL/EVs/2bk_faces.txt to ../../../scratch/alpine/alar6830/WM_All/991267/RL/metadata/2bk_faces.txt
download: s3://hcp-openaccess/HCP_1200/991267/MNINonLinear/Results/tfMRI_WM_RL/EVs/0bk_tools.txt to ../../../scratch/alpine/alar6830/WM_All/9

download: s3://hcp-openaccess/HCP_1200/992673/MNINonLinear/Results/tfMRI_WM_RL/EVs/all_bk_cor.txt to ../../../scratch/alpine/alar6830/WM_All/992673/RL/metadata/all_bk_cor.txt
download: s3://hcp-openaccess/HCP_1200/992673/MNINonLinear/Results/tfMRI_WM_RL/EVs/0bk_faces.txt to ../../../scratch/alpine/alar6830/WM_All/992673/RL/metadata/0bk_faces.txt
download: s3://hcp-openaccess/HCP_1200/992673/MNINonLinear/Results/tfMRI_WM_RL/EVs/0bk_cor.txt to ../../../scratch/alpine/alar6830/WM_All/992673/RL/metadata/0bk_cor.txt
download: s3://hcp-openaccess/HCP_1200/992673/MNINonLinear/Results/tfMRI_WM_RL/EVs/0bk_err.txt to ../../../scratch/alpine/alar6830/WM_All/992673/RL/metadata/0bk_err.txt
download: s3://hcp-openaccess/HCP_1200/992673/MNINonLinear/Results/tfMRI_WM_RL/EVs/all_bk_err.txt to ../../../scratch/alpine/alar6830/WM_All/992673/RL/metadata/all_bk_err.txt
download: s3://hcp-openaccess/HCP_1200/992673/MNINonLinear/Results/tfMRI_WM_RL/EVs/0bk_nlr.txt to ../../../scratch/alpine/alar6830/WM_All/9

download: s3://hcp-openaccess/HCP_1200/993675/MNINonLinear/Results/tfMRI_WM_LR/EVs/WM_Stats.csv to ../../../scratch/alpine/alar6830/WM_All/993675/LR/metadata/WM_Stats.csv
download: s3://hcp-openaccess/HCP_1200/993675/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_faces.txt to ../../../scratch/alpine/alar6830/WM_All/993675/LR/metadata/0bk_faces.txt
download: s3://hcp-openaccess/HCP_1200/993675/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_err.txt to ../../../scratch/alpine/alar6830/WM_All/993675/LR/metadata/0bk_err.txt
download: s3://hcp-openaccess/HCP_1200/993675/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_cor.txt to ../../../scratch/alpine/alar6830/WM_All/993675/LR/metadata/0bk_cor.txt
download: s3://hcp-openaccess/HCP_1200/993675/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_nlr.txt to ../../../scratch/alpine/alar6830/WM_All/993675/LR/metadata/0bk_nlr.txt
download: s3://hcp-openaccess/HCP_1200/993675/MNINonLinear/Results/tfMRI_WM_LR/EVs/all_bk_err.txt to ../../../scratch/alpine/alar6830/WM_All/993675/L

download: s3://hcp-openaccess/HCP_1200/994273/MNINonLinear/Results/tfMRI_WM_RL/EVs/2bk_err.txt to ../../../scratch/alpine/alar6830/WM_All/994273/RL/metadata/2bk_err.txt
download: s3://hcp-openaccess/HCP_1200/994273/MNINonLinear/Results/tfMRI_WM_RL/EVs/2bk_nlr.txt to ../../../scratch/alpine/alar6830/WM_All/994273/RL/metadata/2bk_nlr.txt
download: s3://hcp-openaccess/HCP_1200/994273/MNINonLinear/Results/tfMRI_WM_RL/EVs/2bk_tools.txt to ../../../scratch/alpine/alar6830/WM_All/994273/RL/metadata/2bk_tools.txt
download: s3://hcp-openaccess/HCP_1200/994273/MNINonLinear/Results/tfMRI_WM_RL/EVs/2bk_places.txt to ../../../scratch/alpine/alar6830/WM_All/994273/RL/metadata/2bk_places.txt
download: s3://hcp-openaccess/HCP_1200/994273/MNINonLinear/Results/tfMRI_WM_RL/EVs/Sync.txt to ../../../scratch/alpine/alar6830/WM_All/994273/RL/metadata/Sync.txt
download: s3://hcp-openaccess/HCP_1200/994273/MNINonLinear/Results/tfMRI_WM_RL/EVs/0bk_faces.txt to ../../../scratch/alpine/alar6830/WM_All/994273/RL/m

996782
download: s3://hcp-openaccess/HCP_1200/996782/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_places.txt to ../../../scratch/alpine/alar6830/WM_All/996782/LR/metadata/0bk_places.txt
download: s3://hcp-openaccess/HCP_1200/996782/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_tools.txt to ../../../scratch/alpine/alar6830/WM_All/996782/LR/metadata/0bk_tools.txt
download: s3://hcp-openaccess/HCP_1200/996782/MNINonLinear/Results/tfMRI_WM_LR/EVs/2bk_cor.txt to ../../../scratch/alpine/alar6830/WM_All/996782/LR/metadata/2bk_cor.txt
download: s3://hcp-openaccess/HCP_1200/996782/MNINonLinear/Results/tfMRI_WM_LR/EVs/2bk_body.txt to ../../../scratch/alpine/alar6830/WM_All/996782/LR/metadata/2bk_body.txt
download: s3://hcp-openaccess/HCP_1200/996782/MNINonLinear/Results/tfMRI_WM_LR/EVs/0bk_body.txt to ../../../scratch/alpine/alar6830/WM_All/996782/LR/metadata/0bk_body.txt
download: s3://hcp-openaccess/HCP_1200/996782/MNINonLinear/Results/tfMRI_WM_LR/EVs/2bk_nlr.txt to ../../../scratch/alpine/alar6830/WM_

In [6]:
import os
import numpy as np
import nibabel as nib
import torch



# Define the root directory
root_dir = "/scratch/alpine/alar6830/WM_nback_labels/"
encodings = ["LR", "RL"]
for subject in subject_values:
    if os.path.exists(os.path.join(root_dir, f"{subject}141.nii.gz")):
        #print(f"done with {subject}")
        continue
              
    for enc in encodings:
        # Load the NIfTI image using MONAI's LoadImage
        image_path = f"/scratch/alpine/alar6830/WM_All/{subject}/{enc}/tfMRI_WM_{enc}.nii.gz"

        try:
            full_data = nib.load(image_path)
            full_data = full_data.get_fdata()  # Convert to NumPy array
            print(f"Loaded image for participant: {subject}, shape: {full_data.shape}")
        except Exception as e:
            print(f"Error loading image for participant {subject}: {e}")
            continue
        onset_paths = f"/scratch/alpine/alar6830/WM_All/{subject}/{enc}/metadata/"
        if not os.path.exists(onset_paths):
            print(f"grabbing metadata for {subject}")
            os.mkdir(onset_paths)
            aws_command = f"aws s3 cp  s3://hcp-openaccess/HCP_1200/{subject}/MNINonLinear/Results/tfMRI_WM_{enc}/EVs/ {onset_paths} --recursive"
            !{aws_command}
    
        zero_body = np.loadtxt(onset_paths+"0bk_body.txt")[0:2]
        zero_faces = np.loadtxt(onset_paths+"0bk_faces.txt")[0:2]
        zero_places = np.loadtxt(onset_paths+"0bk_places.txt")[0:2]
        zero_tools = np.loadtxt(onset_paths+"0bk_tools.txt")[0:2]
        two_body = np.loadtxt(onset_paths+"2bk_body.txt")[0:2]
        two_faces = np.loadtxt(onset_paths+"2bk_faces.txt")[0:2]
        two_places = np.loadtxt(onset_paths+"2bk_places.txt")[0:2]
        two_tools = np.loadtxt(onset_paths+"2bk_tools.txt")[0:2]
    
        data_dict = {
            10: zero_body,
            20: zero_faces,
            30: zero_places,
            40: zero_tools,
            11: two_body,
            21: two_faces,
            31: two_places,
            41: two_tools
        }
        for key,value in data_dict.items():
            try:
                onset = seconds_to_frame(value[0] +2.5) #do not include cue/rest at the beginning
                offset = seconds_to_frame(value[1] + value[0])

                cropped_image = full_data[:,:,:,onset:offset]

                img = nib.Nifti1Image(cropped_image, None)

                if enc == "LR":
                    enc_num = 0
                else:
                    enc_num = 1
                # Apply the SaveImage transform to save the image
                nib.save(img, os.path.join(root_dir, f"{subject}{enc_num}{key}.nii.gz"))
            except:
                print(f"onsets {key} not properly formatted for {subject}")
                
            
            
            
    
        
            
        
        
          
        
    
    

Error loading image for participant 116120: No such file or no access: '/scratch/alpine/alar6830/WM_All/116120/LR/tfMRI_WM_LR.nii.gz'
Error loading image for participant 116120: No such file or no access: '/scratch/alpine/alar6830/WM_All/116120/RL/tfMRI_WM_RL.nii.gz'
Error loading image for participant 126931: No such file or no access: '/scratch/alpine/alar6830/WM_All/126931/LR/tfMRI_WM_LR.nii.gz'
Error loading image for participant 126931: No such file or no access: '/scratch/alpine/alar6830/WM_All/126931/RL/tfMRI_WM_RL.nii.gz'
Error loading image for participant 129432: No such file or no access: '/scratch/alpine/alar6830/WM_All/129432/LR/tfMRI_WM_LR.nii.gz'
Error loading image for participant 129432: No such file or no access: '/scratch/alpine/alar6830/WM_All/129432/RL/tfMRI_WM_RL.nii.gz'
Error loading image for participant 129533: No such file or no access: '/scratch/alpine/alar6830/WM_All/129533/LR/tfMRI_WM_LR.nii.gz'
Error loading image for participant 129533: No such file or no